In [12]:
# Common imports
import argparse
import time
import numpy as np
import os
from datetime import datetime
import sys; sys.path.append('../deepdown/')

# Import torch
from torch.utils.data import Dataset
from deepdown.utils.data_generators import DataGenerator
import torch

# Utils
from utils.data_loader import load_target_data, load_input_data
from utils.loss_fcts import *
from utils.data_generators import DataGenerator
from utils.helpers import print_cuda_availability, DEVICE
from models.srgan import Generator, Discriminator
from config import Config

### Read the configuration file and load the data

In [3]:
from argparse import Namespace
cli_args = Namespace(config_file="../config.yaml")
conf = Config(cli_args)
conf.print()

In [5]:
# Date parameters
date_start = conf.config.date_start
date_end = conf.config.date_end

# Years for training, validation, and testing
years_train = conf.config.years_train
years_valid = conf.config.years_valid
years_test = conf.config.years_test

# Other parameters
levels = conf.config.levels
resol_low = conf.config.resol_low

# Input variables and paths
input_variables = conf.config.input_vars
input_paths = [
    conf.config.path_era5land + '/precipitation',
    conf.config.path_era5land + '/temperature',
    conf.config.path_era5land + '/max_temperature/',
    conf.config.path_era5land + '/min_temperature/'
]

# Crop parameters
do_crop = conf.config.do_crop
crop_x = conf.config.lon_limits
crop_y = conf.config.lat_limits


In [6]:

# Load target data
target = load_target_data(date_start, date_end, conf.config.path_mch,
                              path_tmp=conf.config.path_tmp)

# Extract the axes of the final target domain based on temperature 
x_axis = target.TabsD.x
y_axis = target.TabsD.y

Target data loaded from pickle.


In [7]:
input_data = load_input_data(date_start, date_end, conf.config.path_dem,
                                 input_variables, input_paths,
                                 levels, resol_low, x_axis, y_axis,
                                 path_tmp=conf.config.path_tmp)



Extracting input data...
Extracting data for the period 1979-01-01 - 2021-12-31
Extracting data for the period 1979-01-01 - 2021-12-31
Extracting data for the period 1979-01-01 - 2021-12-31
Extracting data for the period 1979-01-01 - 2021-12-31


In [20]:
if do_crop:
    input_data = input_data.sel(x=slice(min(crop_x), max(crop_x)),
                                    y=slice(max(crop_y), min(crop_y)))
    target = target.sel(x=slice(min(crop_x), max(crop_x)),
                            y=slice(max(crop_y), min(crop_y)))

# Split the data
x_train = input_data.sel(time=slice( datetime(years_train[0],1,1), datetime(years_train[1], 12, 31)))
x_valid = input_data.sel(time=slice( datetime(years_valid[0],1,1), datetime(years_valid[1], 12, 31)))
x_test = input_data.sel(time=slice( datetime(years_test[0],1,1), datetime(years_test[1], 12, 31)))

y_train = target.sel(time=slice( datetime(years_train[0],1,1), datetime(years_train[1], 12, 31)))
y_valid = target.sel(time=slice( datetime(years_valid[0],1,1), datetime(years_valid[1], 12, 31)))
y_test = target.sel(time=slice( datetime(years_test[0],1,1), datetime(years_test[1], 12, 31)))



In [33]:
# Select the variables to use as input and output
input_vars = {'band_data': None, 'tp': None, 't2m': None, 't2m_min': None, 't2m_max': None}
output_vars = ['RhiresD', 'TabsD']  # ['RhiresD', 'TabsD', 'TmaxD', 'TminD']

In [34]:
training_set = DataGenerator(x_train, y_train, input_vars, output_vars)
loader_train = torch.utils.data.DataLoader(training_set, batch_size=32)
valid_set = DataGenerator(x_valid, y_valid, input_vars, output_vars, shuffle=False,
                              mean=training_set.mean, std=training_set.std)
loader_val = torch.utils.data.DataLoader(valid_set, batch_size=32)
test_set = DataGenerator(x_test, y_test, input_vars, output_vars, shuffle=False,
                             mean=training_set.mean, std=training_set.std)
loader_test = torch.utils.data.DataLoader(test_set, batch_size=32)

HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 1:
  #000: H5A.c line 528 in H5Aopen_by_name(): can't open attribute
    major: Attribute
    minor: Can't open object
  #001: H5VLcallback.c line 1091 in H5VL_attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #002: H5VLcallback.c line 1058 in H5VL__attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #003: H5VLnative_attr.c line 130 in H5VL__native_attr_open(): can't open attribute
    major: Attribute
    minor: Can't open object
  #004: H5Aint.c line 545 in H5A__open_by_name(): unable to load attribute info from object header
    major: Attribute
    minor: Unable to initialize object
  #005: H5Oattribute.c line 494 in H5O__attr_open_by_name(): can't locate attribute: '_QuantizeBitGroomNumberOfSignificantDigits'
    major: Attribute
    minor: Object not found
HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 1:
  #000: H5A.c line 528 in H5Ao

Loading data into RAM


HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 88:
  #000: H5A.c line 528 in H5Aopen_by_name(): can't open attribute
    major: Attribute
    minor: Can't open object
  #001: H5VLcallback.c line 1091 in H5VL_attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #002: H5VLcallback.c line 1058 in H5VL__attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #003: H5VLnative_attr.c line 130 in H5VL__native_attr_open(): can't open attribute
    major: Attribute
    minor: Can't open object
  #004: H5Aint.c line 545 in H5A__open_by_name(): unable to load attribute info from object header
    major: Attribute
    minor: Unable to initialize object
  #005: H5Oattribute.c line 494 in H5O__attr_open_by_name(): can't locate attribute: '_QuantizeBitGroomNumberOfSignificantDigits'
    major: Attribute
    minor: Object not found
HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 88:
  #000: H5A.c line 528 in H5

Loading data into RAM


HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 83:
  #000: H5A.c line 528 in H5Aopen_by_name(): can't open attribute
    major: Attribute
    minor: Can't open object
  #001: H5VLcallback.c line 1091 in H5VL_attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #002: H5VLcallback.c line 1058 in H5VL__attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #003: H5VLnative_attr.c line 130 in H5VL__native_attr_open(): can't open attribute
    major: Attribute
    minor: Can't open object
  #004: H5Aint.c line 545 in H5A__open_by_name(): unable to load attribute info from object header
    major: Attribute
    minor: Unable to initialize object
  #005: H5Oattribute.c line 494 in H5O__attr_open_by_name(): can't locate attribute: '_QuantizeBitGroomNumberOfSignificantDigits'
    major: Attribute
    minor: Object not found
HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 83:
  #000: H5A.c line 528 in H5

Loading data into RAM


HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 37:
  #000: H5A.c line 528 in H5Aopen_by_name(): can't open attribute
    major: Attribute
    minor: Can't open object
  #001: H5VLcallback.c line 1091 in H5VL_attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #002: H5VLcallback.c line 1058 in H5VL__attr_open(): attribute open failed
    major: Virtual Object Layer
    minor: Can't open object
  #003: H5VLnative_attr.c line 130 in H5VL__native_attr_open(): can't open attribute
    major: Attribute
    minor: Can't open object
  #004: H5Aint.c line 545 in H5A__open_by_name(): unable to load attribute info from object header
    major: Attribute
    minor: Unable to initialize object
  #005: H5Oattribute.c line 494 in H5O__attr_open_by_name(): can't locate attribute: '_QuantizeBitGroomNumberOfSignificantDigits'
    major: Attribute
    minor: Object not found
HDF5-DIAG: Error detected in HDF5 (1.12.2) thread 37:
  #000: H5A.c line 528 in H5